In [2]:
from IPython.display import clear_output
import pandas as pd 
import subprocess #run R code from subprocess
import numpy as np
from os import listdir # get dir list
from os.path import isfile, join # get dir list


import concurrent.futures
import time
from sklearn.neighbors import KNeighborsClassifier
from sklearn.model_selection import KFold, cross_validate
from sklearn.model_selection import cross_val_score, cross_validate
from sklearn.metrics import make_scorer, accuracy_score, precision_score, recall_score, f1_score, roc_auc_score
from sklearn.tree import DecisionTreeClassifier
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.multioutput import MultiOutputClassifier
import pickle

In [3]:
def buldDictOfDatasetsByNumber(df):
    indexList = df.index
    numberDict ={}
    for i in indexList:
        n = i.split('_')[0]
        if n in numberDict:
            numberDict[n].append(i)
        else:
            numberDict[n] = [i]
    return numberDict

In [79]:
pd.read_csv('Metabases/metabases_Multiple_Classifiers/Metabase_DT.csv.zip', index_col='Dataset')

attr_conc.mean  attr_conc.sd  \
Dataset                                                            
1004_synthetic_control_10_0.csv.gz    8.331300e-02      0.062438   
1004_synthetic_control_10_1.csv.gz    1.005420e-01      0.057744   
1004_synthetic_control_10_2.csv.gz    8.331762e-02      0.067932   
1004_synthetic_control_10_3.csv.gz    6.843893e-02      0.060531   
1004_synthetic_control_10_4.csv.gz    6.317691e-02      0.059250   
...                                            ...           ...   
997_balance-scale_5_5.csv.gz         -6.250002e-08      0.000000   
997_balance-scale_5_6.csv.gz         -6.250002e-08      0.000000   
997_balance-scale_5_7.csv.gz         -6.250002e-08      0.000000   
997_balance-scale_5_8.csv.gz         -6.250002e-08      0.000000   
997_balance-scale_5_9.csv.gz         -6.250002e-08      0.000000   

                                    attr_ent.mean  attr_ent.sd  attr_to_inst  \
Dataset                                                                        
1004_synthetic_control_10_0.csv.gz       2.999999     0.000006        0.1000   
1004_synthetic_control_10_1.csv.gz       2.999999     0.000006        0.1000   
1004_synthetic_control_10_2.csv.gz       2.999999     0.000006        0.1000   
1004_synthetic_control_10_3.csv.gz       2.999999     0.000006        0.1000   
1004_synthetic_control_10_4.csv.gz       2.999999     0.000006        0.1000   
...                                           ...          ...           ...   
997_balance-scale_5_5.csv.gz             2.321928     0.000000        0.0064   
997_balance-scale_5_6.csv.gz             2.321928     0.000000        0.0064   
997_balance-scale_5_7.csv.gz             2.321928     0.000000        0.0064   
997_balance-scale_5_8.csv.gz             2.321928     0.000000        0.0064   
997_balance-scale_5_9.csv.gz             2.321928     0.000000        0.0064   

                                    best_node.mean  best_node.sd  \
Dataset                                                            
1004_synthetic_control_10_0.csv.gz        0.878333      0.076965   
1004_synthetic_control_10_1.csv.gz        0.885000      0.084451   
1004_synthetic_control_10_2.csv.gz        0.875000      0.087995   
1004_synthetic_control_10_3.csv.gz        0.861667      0.078969   
1004_synthetic_control_10_4.csv.gz        0.870000      0.083458   
...                                            ...           ...   
997_balance-scale_5_5.csv.gz              0.512000      0.043451   
997_balance-scale_5_6.csv.gz              0.507200      0.040635   
997_balance-scale_5_7.csv.gz              0.504000      0.035327   
997_balance-scale_5_8.csv.gz              0.537600      0.051350   
997_balance-scale_5_9.csv.gz              0.497600      0.050723   

                                    can_cor.mean  cat_to_num  class_conc.mean  \
Dataset                                                                         
1004_synthetic_control_10_0.csv.gz      0.688118         0.0         0.012346   
1004_synthetic_control_10_1.csv.gz      0.707928         0.0         0.012193   
1004_synthetic_control_10_2.csv.gz      0.729191         0.0         0.012570   
1004_synthetic_control_10_3.csv.gz      0.718893         0.0         0.012131   
1004_synthetic_control_10_4.csv.gz      0.718633         0.0         0.012191   
...                                          ...         ...              ...   
997_balance-scale_5_5.csv.gz            0.709977         0.0         0.032749   
997_balance-scale_5_6.csv.gz            0.711547         0.0         0.032597   
997_balance-scale_5_7.csv.gz            0.729005         0.0         0.034303   
997_balance-scale_5_8.csv.gz            0.714676         0.0         0.033294   
997_balance-scale_5_9.csv.gz            0.713556         0.0         0.032907   

                                    ...  worst_node.sd  BestType  \
Dataset                             ...                            
1004_synthetic_control_10_0.csv.gz 

In [4]:
df = pd.read_csv('Metabases/metabases_Multiple_Classifiers/Metabase_DT.csv.zip', index_col='Dataset')
numberDict = buldDictOfDatasetsByNumber(df)
cols = list(range(0, 97))
type = 'DT'
df0 = pd.DataFrame()
features = []
count = 0
for i in numberDict:
    RF = RandomForestClassifier(random_state=0, n_jobs=60)
    train = df.drop(df.loc[numberDict[i],:].index, axis =0)
    pred = df.loc[numberDict[i],:]
#     X = train.iloc[:, : 73]
    X = train.iloc[:, cols]
    y = train.iloc[:, 97: ]
    RF.fit(X, y)
    result = RF.predict(pred.iloc[:, cols])
#     result = RF.predict(pred.iloc[:, : 73])
    resultDF = pd.DataFrame(result, columns = pred.columns[97:])
    resultDF.index = pred.index
    if df0.empty:
        df0 = resultDF.copy()
        features = RF.feature_importances_
    else:
        df0 = df0.append(resultDF.copy())
        features = np.append(features, RF.feature_importances_)
    clear_output(wait=True)
    count +=1
    print ("exec - "+ type + ' -' + str(count) + " / " + str(len(numberDict)))

exec - DT -358 / 358


In [43]:
a = {}
if  'a' in a:
    a[2] = np.append(a[2], RF.feature_importances_)
else:
    a[2] = RF.feature_importances_

a[2]


# RF.feature_importances_
df

97

In [37]:
from sklearn import preprocessing
le = preprocessing.LabelEncoder()
X = le.fit_transform(df[['BestType']])
X


cols = df.iloc[:,:97].columns
cols
test = GradientBoostingClassifier(random_state=0)
test.fit(df[cols], X)

/home/lpfgarcia/pedropio/NoiseSelection/NoiseEnvPy/lib/python3.8/site-packages/sklearn/preprocessing/_label.py:115: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


KeyboardInterrupt: 

In [9]:
def trainGBAndReturnPredictions(cols = None, metricName = None, numberDict = None, version = None):
    # if cols == None:
    #     cols = df.iloc[:, :97].columns
    df = pd.read_csv(f'Metabases/metabases_Multiple_Classifiers/Metabase_{version}.csv.zip', index_col='Dataset')
    df0 = pd.DataFrame()
    features = {}
    count = 0
    labels = []
    if version in ['DT', 'RF', 'KNN', 'SVM']:
        # print('oi')
        labels = ['BestType', 'BestEnsambleAlgo', 'BestDistanceAlgo', 'BestVotingAlgo',
            'BestAenn', 'BestGE', 'BestOR', 'BestEdge', 'BestHARF']
    else:
        labels = ['BestType', 'BestEnsambleAlgo', 'BestDistanceAlgo', 'BestVotingAlgo']
            
    for i in numberDict:
        
        GB = MultiOutputClassifier(GradientBoostingClassifier(random_state=0), n_jobs = len(labels))
        train = df.drop(df.loc[numberDict[i],:].index, axis =0)
        pred = df.loc[numberDict[i],:]
    #     X = train.iloc[:, : 73]
        X = train[cols]
        y = train[labels]
        GB.fit(X, y)
        for index, label in enumerate(labels):
            if  label in features:
                # print(label)
                features[label] = np.append(features[label], GB.estimators_[index].feature_importances_)
            else:
                # print(label)
                features[label] = GB.estimators_[index].feature_importances_
        result = GB.predict(pred[cols])    
        resultDF = pd.DataFrame(result, columns = labels)
        resultDF.index = pred.index
        if df0.empty:
            df0 = resultDF.copy()
        else:
            df0 = df0.append(resultDF.copy())
        clear_output(wait=True)
        count +=1
        print ("exec - "+ version  +' - '  + str(count) + " / " + str(len(numberDict)))
    df0.index = df.index
    df0.to_csv(f'MultipleClassifierResults/results_Multiple_GB_{metricName}-{version}.csv.zip')
    for label in features:
        features[label] = np.array_split(features[label], len(numberDict))
    features['cols'] = cols
    pickle.dump(features, open(f'MultipleClassifierResults/features_GB_{metricName}-{version}.p', "wb"))  # save it into a file named save.p
    return df0, features


In [11]:
versions = ['SVM', 'SVM_NoHyper']
df = pd.read_csv('Metabases/metabases_Multiple_Classifiers/Metabase_DT.csv.zip', index_col='Dataset')
# df = pd.read_csv(f'Metabases/metabases_Multiple_Classifiers/Metabase_{version[0]}.csv.zip', index_col='Dataset')
numberDict = buldDictOfDatasetsByNumber(df)
smallNumDict = {}
count1 = 0
for i in numberDict:
    smallNumDict[i] = numberDict[i].copy()
    count1 +=1
    if count1 >=2:
        break
cols = df.iloc[:,:97].columns
metricName = 'f1-score'
start = time.perf_counter()
trainGBAndReturnPredictions( cols , metricName, numberDict, versions[0])
end = time.perf_counter()
print(f'tempo total: {int((end-start)/60)} min {int((end-start)%60)} s' )

exec - SVM - 358 / 358
tempo total: 481 min 4 s


In [4]:
versions = ['SVM', 'SVM_NoHyper']
df = pd.read_csv('Metabases/metabases_Multiple_Classifiers/Metabase_DT.csv.zip', index_col='Dataset')
# df = pd.read_csv(f'Metabases/metabases_Multiple_Classifiers/Metabase_{version[0]}.csv.zip', index_col='Dataset')
numberDict = buldDictOfDatasetsByNumber(df)
smallNumDict = {}
count1 = 0
for i in numberDict:
    smallNumDict[i] = numberDict[i].copy()
    count1 +=1
    if count1 >=2:
        break
cols = df.iloc[:,:97].columns
metricName = 'f1-score'
start = time.perf_counter()
with concurrent.futures.ProcessPoolExecutor(3) as executor:
#                 results = executor.map(runMFE, smallSet)
    # smallNumDict
    results = [executor.submit(trainGBAndReturnPredictions, cols , metricName, numberDict, version) for version in versions]
    # results = [executor.submit(trainGBAndReturnPredictions, cols , metricName, smallNumDict, version) for version in versions]
    for s in concurrent.futures.as_completed(results):
        end = time.perf_counter()
        print(f'tempo total: {int((end-start)/60)} min {int((end-start)%60)} s' )
# trainGBAndReturnPredictions(cols, metricName, numberDict, versions[0])

exec - SVM - 358 / 358
tempo total: 531 min 56 s


/home/lpfgarcia/pedropio/NoiseSelection/NoiseEnvPy/lib/python3.8/site-packages/joblib/externals/loky/backend/resource_tracker.py:318: UserWarning: resource_tracker: There appear to be 716 leaked folder objects to clean up at shutdown
  warnings.warn('resource_tracker: There appear to be %d '
/home/lpfgarcia/pedropio/NoiseSelection/NoiseEnvPy/lib/python3.8/site-packages/joblib/externals/loky/backend/resource_tracker.py:318: UserWarning: resource_tracker: There appear to be 716 leaked folder objects to clean up at shutdown
  warnings.warn('resource_tracker: There appear to be %d '


In [41]:
# df = pd.read_csv(f'Metabases/metabases_Multiple_Classifiers/Metabase_{versions[0]}.csv.zip', index_col='Dataset')
# df[['BestType', 'BestEnsambleAlgo', 'BestDistanceAlgo', 'BestVotingAlgo',
#             'BestAenn', 'BestGE', 'BestOR', 'BestEdge', 'BestHARF']]
versions = ['DT', 'RF', 'KNN', 'DT_NoHyper', 'RF_NoHyper', 'KNN_NoHyper']
trainGBAndReturnPredictions(cols, metricName, numberDict, versions[0])

oi


KeyboardInterrupt: 

In [5]:
df = pd.read_csv(f'Metabases/metabases_Multiple_Classifiers/Metabase_SVM.csv.zip', index_col='Dataset')
numberDict = buldDictOfDatasetsByNumber(df)
smallNumDict = {}
count1 = 0
for i in numberDict:
    smallNumDict[i] = numberDict[i].copy()
    count1 +=1
    if count1 >=2:
        break
len(smallNumDict)

2

NameError: name 'smallNumDict' is not defined

In [5]:
# trainGBAndReturnPredictions(cols , metricName, smallNumDict, 'DT')
pd.read_csv(f'MultipleClassifierResults/results_Multiple_GB_f1-score-DT.csv.zip', index_col='Dataset')

Ensamble    8448
Voting      1654
Distance     638
Name: BestType, dtype: int64

In [42]:
# versions = ['DT', 'RF', 'KNN', 'DT_NoHyper', 'RF_NoHyper', 'KNN_NoHyper']
versions = ['DT', 'RF', 'KNN']
cols = df.iloc[:,:97].columns
metricName = 'f1-score'
start = time.perf_counter()
with concurrent.futures.ProcessPoolExecutor(3) as executor:
#                 results = executor.map(runMFE, smallSet)
    smallNumDict
    results = [executor.submit(trainGBAndReturnPredictions, cols , metricName, numberDict, version) for version in versions]
    # results = [executor.submit(trainGBAndReturnPredictions, cols , metricName, smallNumDict, version) for version in versions]
    for s in concurrent.futures.as_completed(results):
        end = time.perf_counter()
        print(f'tempo total: {int((end-start)/60)} min {int((end-start)%60)} s' )

exec - DT - 358 / 358
tempo total: 1000 min 12 s


In [85]:
baseLearners = ['DT', 'RF', 'KNN']
versions = ['Hyper', 'NoHyper']
for version in versions:
    for baseLearner in baseLearners:
        if version == 'Hyper':
            df = pd.read_csv(f'Metabases/metabases_Multiple_Classifiers/Metabase_{baseLearner}.csv.zip', index_col='Dataset')
            labels = ['BestType', 'BestEnsambleAlgo', 'BestDistanceAlgo', 'BestVotingAlgo',
            'BestAenn', 'BestGE', 'BestOR', 'BestEdge', 'BestHARF']
        else:
            df = pd.read_csv(f'Metabases/metabases_Multiple_Classifiers/Metabase_{baseLearner}_NoHyper.csv.zip', index_col='Dataset')
            labels = ['BestType', 'BestEnsambleAlgo', 'BestDistanceAlgo', 'BestVotingAlgo']
            
        numberDict = buldDictOfDatasetsByNumber(df)
        cols = df.iloc[:,:97].columns
        # labels = ['BestType', 'BestEnsambleAlgo', 'BestDistanceAlgo', 'BestVotingAlgo',
        #     'BestAenn', 'BestGE', 'BestOR', 'BestEdge', 'BestHARF']
        metricName = 'f1-score'

        a, b = trainGBAndReturnPredictions(df, cols , metricName, numberDict , baseLearner , labels, version)

BestType
BestEnsambleAlgo


KeyboardInterrupt: 

In [64]:
b['BestEnsambleAlgo']

[array([1.01003552e-02, 1.03338411e-02, 1.21274950e-02, 8.45561366e-03,
        6.72673044e-03, 1.75550092e-02, 1.45433501e-02, 1.48541554e-02,
        0.00000000e+00, 1.34044660e-02, 1.41135763e-02, 2.22282571e-02,
        6.10213294e-03, 3.63033218e-03, 5.00992713e-03, 1.55337044e-02,
        1.35029827e-02, 1.32943939e-02, 0.00000000e+00, 2.26431844e-02,
        1.59692694e-02, 6.04669560e-03, 4.73633133e-03, 3.92977255e-03,
        2.97546908e-02, 2.26302539e-02, 2.21665634e-02, 1.25068871e-02,
        1.08317237e-02, 1.20552717e-02, 1.20775425e-02, 1.10486893e-02,
        1.50162806e-02, 1.16931367e-02, 1.12131195e-02, 1.71975149e-05,
        1.48338520e-02, 1.38639158e-02, 3.66285276e-03, 4.45731631e-03,
        3.38009398e-03, 3.07873370e-03, 7.45697185e-03, 7.36161363e-03,
        4.64305414e-03, 4.48528249e-03, 6.41319248e-03, 4.12589521e-03,
        1.37470481e-02, 1.43938732e-02, 1.77180927e-02, 1.48225441e-02,
        1.09627176e-02, 1.25215508e-02, 1.52069941e-02, 1.276135

In [7]:
# def trainRFAndReturnPredictions(df= None, cols = list(range(0, 97)), metricName = None, numberDict = None, type = None):

df = pd.read_csv('Metabases/metabases_Multiple_Classifiers/Metabase_DT.csv.zip', index_col='Dataset')
numberDict = buldDictOfDatasetsByNumber(df)
cols = list(range(0, 97))
type = 'DT'
df0 = pd.DataFrame()
features = []
count = 0
labels = ['BestType', 'BestEnsambleAlgo', 'BestDistanceAlgo', 'BestVotingAlgo',
       'BestAenn', 'BestGE', 'BestOR', 'BestEdge', 'BestHARF']
for i in numberDict:
    results = []
    for label in labels:
        RF = RandomForestClassifier(random_state=0, n_jobs=70)
        train = df.drop(df.loc[numberDict[i],:].index, axis =0)
        pred = df.loc[numberDict[i],:]
    #     X = train.iloc[:, : 73]
        X = train.iloc[:, cols]
        y = train[label]
        RF.fit(X, y)
        result = RF.predict(pred.iloc[:, cols])
    #     result = RF.predict(pred.iloc[:, : 73])
        results.append(result)
    resultDF = pd.DataFrame(np.array(results).T, columns = labels)
    if df0.empty:
        df0 = resultDF.copy()
        features = RF.feature_importances_
    else:
        df0 = df0.append(resultDF.copy())
        features = np.append(features, RF.feature_importances_)
    clear_output(wait=True)
    count +=1
    print ("exec - "+ type + ' -' + str(count) + " / " + str(len(numberDict)))
df0.index = df.index
df0.to_csv(f'RankingResults/results_Multiple_RF_f1-score-DT.csv.zip')

exec - DT -358 / 358


AttributeError: 'DataFrame' object has no attribute 'to_csvto_csv'

In [13]:
df = pd.read_csv('Metabases/metabases_Multiple_Classifiers/Metabase_DT_NoHyper.csv.zip', index_col='Dataset')
numberDict = buldDictOfDatasetsByNumber(df)
cols = list(range(0, 97))
type = 'DT'
df1 = pd.DataFrame()
features = []
count = 0
labels = ['BestType', 'BestEnsambleAlgo', 'BestDistanceAlgo', 'BestVotingAlgo']
for i in numberDict:
    results = []
    for label in labels:
        RF = RandomForestClassifier(random_state=0, n_jobs=70)
        train = df.drop(df.loc[numberDict[i],:].index, axis =0)
        pred = df.loc[numberDict[i],:]
    #     X = train.iloc[:, : 73]
        X = train.iloc[:, cols]
        y = train[label]
        RF.fit(X, y)
        result = RF.predict(pred.iloc[:, cols])
    #     result = RF.predict(pred.iloc[:, : 73])
        results.append(result)
    resultDF = pd.DataFrame(np.array(results).T, columns = labels)
    if df1.empty:
        df1 = resultDF.copy()
        features = RF.feature_importances_
    else:
        df1 = df1.append(resultDF.copy())
        features = np.append(features, RF.feature_importances_)
    clear_output(wait=True)
    count +=1
    print ("exec - "+ type + ' -' + str(count) + " / " + str(len(numberDict)))
df1.index = df.index
df1.to_csv(f'RankingResults/results_Multiple_RF_f1-score-DT-NoHyper.csv.zip')

exec - DT -358 / 358


In [15]:
df1.index = df.index
df1.to_csv(f'RankingResults/results_Multiple_RF_f1-score-DT-NoHyper.csv.zip')
df1

BestType BestEnsambleAlgo BestDistanceAlgo  \
Dataset                                                                         
1004_synthetic_control_10_0.csv.gz   Voting          ORBoost             AENN   
1004_synthetic_control_10_1.csv.gz   Voting          ORBoost             AENN   
1004_synthetic_control_10_2.csv.gz   Voting          ORBoost             AENN   
1004_synthetic_control_10_3.csv.gz   Voting          ORBoost             AENN   
1004_synthetic_control_10_4.csv.gz   Voting             Edge             AENN   
...                                     ...              ...              ...   
997_balance-scale_5_5.csv.gz         Voting          ORBoost             AENN   
997_balance-scale_5_6.csv.gz         Voting          ORBoost             AENN   
997_balance-scale_5_7.csv.gz         Voting          ORBoost             AENN   
997_balance-scale_5_8.csv.gz         Voting          ORBoost             AENN   
997_balance-scale_5_9.csv.gz         Voting          ORBoost             AENN   

                                   BestVotingAlgo  
Dataset                                            
1004_synthetic_control_10_0.csv.gz        Dynamic  
1004_synthetic_control_10_1.csv.gz        Dynamic  
1004_synthetic_control_10_2.csv.gz        Dynamic  
1004_synthetic_control_10_3.csv.gz        Dynamic  
1004_synthetic_control_10_4.csv.gz        Dynamic  
...                                           ...  
997_balance-scale_5_5.csv.gz              Dynamic  
997_balance-scale_5_6.csv.gz              Dynamic  
997_balance-scale_5_7.csv.gz              Dynamic  
997_balance-scale_5_8.csv.gz              Dynamic  
997_balance-scale_5_9.csv.gz              Dynamic  

[10740 rows x 4 columns]

In [23]:
df1['BestType'].value_counts()

Voting      7018
Ensamble    3182
Distance     540
Name: BestType, dtype: int64

In [21]:
df['BestType'].value_counts()

Voting      5620
Ensamble    3836
Distance    1284
Name: BestType, dtype: int64

In [79]:
df0.to_csv('MultiClassifiersResultsRF.csv.zip')

In [25]:
df = pd.read_csv('Metabases/metabases_Multiple_Classifiers/Metabase_DT.csv.zip', index_col='Dataset')
df = pd.read_csv('Metabases/metabases_Multiple_Classifiers/Metabase_DT_NoHyper.csv.zip', index_col='Dataset')
sum(df1['BestType'] == df['BestType']*1)

6263

In [31]:
# sum((df0['BestType'] == df['BestType'])*1)
df = pd.read_csv('Metabases/metabases_Multiple_Classifiers/Metabase_DT.csv.zip', index_col='Dataset')
a = df0[df0.columns] == df.iloc[:, 97: ]
a

BestType  BestEnsambleAlgo  \
Dataset                                                          
1004_synthetic_control_10_0.csv.gz     False              True   
1004_synthetic_control_10_1.csv.gz     False             False   
1004_synthetic_control_10_2.csv.gz     False              True   
1004_synthetic_control_10_3.csv.gz     False              True   
1004_synthetic_control_10_4.csv.gz      True              True   
...                                      ...               ...   
997_balance-scale_5_5.csv.gz           False              True   
997_balance-scale_5_6.csv.gz           False             False   
997_balance-scale_5_7.csv.gz           False             False   
997_balance-scale_5_8.csv.gz           False              True   
997_balance-scale_5_9.csv.gz           False              True   

                                    BestDistanceAlgo  BestVotingAlgo  \
Dataset                                                                
1004_synthetic_control_10_0.csv.gz              True            True   
1004_synthetic_control_10_1.csv.gz              True            True   
1004_synthetic_control_10_2.csv.gz              True            True   
1004_synthetic_control_10_3.csv.gz              True           False   
1004_synthetic_control_10_4.csv.gz             False           False   
...                                              ...             ...   
997_balance-scale_5_5.csv.gz                    True            True   
997_balance-scale_5_6.csv.gz                    True            True   
997_balance-scale_5_7.csv.gz                    True            True   
997_balance-scale_5_8.csv.gz                    True           False   
997_balance-scale_5_9.csv.gz                    True           False   

                                    BestAenn  BestGE  BestOR  BestEdge  \
Dataset                                                                  
1004_synthetic_control_10_0.csv.gz      True   False   False      True   
1004_synthetic_control_10_1.csv.gz      True    True    True      True   
1004_synthetic_control_10_2.csv.gz      True    True   False      True   
1004_synthetic_control_10_3.csv.gz      True    True    True      True   
1004_synthetic_control_10_4.csv.gz      True   False   False      True   
...                                      ...     ...     ...       ...   
997_balance-scale_5_5.csv.gz           False    True   False      True   
997_balance-scale_5_6.csv.gz           False   False   False      True   
997_balance-scale_5_7.csv.gz           False   False   False      True   
997_balance-scale_5_8.csv.gz           False   False   False     False   
997_balance-scale_5_9.csv.gz           False   False   False      True   

                                    BestHARF  
Dataset                                       
1004_synthetic_control_10_0.csv.gz      True  
1004_synthetic_control_10_1.csv.gz     False  
1004_synthetic_control_10_2.csv.gz      True  
1004_synthetic_control_10_3.csv.gz      True  
1004_synthetic_control_10_4.csv.gz     False  
...                                      ...  
997_balance-scale_5_5.csv.gz            True  
997_balance-scale_5_6.csv.gz           False  
997_balance-scale_5_7.csv.gz            True  
997_balance-scale_5_8.csv.gz            True  
997_balance-scale_5_9.csv.gz            True  

[10740 rows x 9 columns]

In [38]:
def returnSelectedAlgorithms(df = None):
    best_algo ={}
    for index, row in df.iterrows():
        best_algo[index] = row[f'Best{row["BestType"]}Algo']
        if best_algo[index] == 'ORBoost':
            best_algo[index] = row['BestOR']
        if best_algo[index] == 'AENN':
            best_algo[index] = row['BestAenn']
        if best_algo[index] == 'GE':
            best_algo[index] = row['BestGE']
        if best_algo[index] == 'HARF':
            best_algo[index]= row['BestHARF']
        if best_algo[index] == 'Edge':
            best_algo[index] = row['BestEdge']
    return pd.DataFrame.from_dict(best_algo, orient= 'index', columns=["SelectedAlgo"])

def getBestAlgorithmsList(metabase):
    meta_data = pd.read_csv(f'Metabases/Metabase_{metabase}.csv.zip', index_col='Dataset').iloc[:,97:]
    rank = pd.DataFrame()
    # meta_data.drop('test_f1_macro_mean_AENN',axis=1, inplace=True)
    for i, a in enumerate(meta_data.index):
        rank = rank.append(meta_data.iloc[i].rank(method = 'dense', ascending = False))
    
    rank.columns = ['Edge5','Edge20', 'HARF85','Hybrid', 'Edge15', 'OR3','GE9', 'AENN7',
       'HARF75', 'OR19','AENN11', 'AENN9','OR11', 'PRISM','GE3', 'GE7',
       'OR15', 'Dynamic','Edge10', 'HARF80','AENN3', 'HARF90','OR7', 'HARF70',
       'GE5', 'AENN5','GE11']

    bestAlgorithmsDict ={}
    bestAlgorithmsList = []
    for index, row in rank.iterrows():
        arr = list(row[row == 1].index)
        bestAlgorithmsDict[index] = arr
        bestAlgorithmsList.append(arr)
    return bestAlgorithmsList, bestAlgorithmsDict

In [39]:
df = pd.read_csv(f'MultiClassifiersResultsRF.csv.zip', index_col='Dataset')
display (df)
df0 = returnSelectedAlgorithms(df)
bestalgoList, bestalgoDict =  getBestAlgorithmsList("DT")
df0['Best'] = bestalgoList
df0

BestType BestEnsambleAlgo  \
Dataset                                                         
1004_synthetic_control_10_0.csv.gz  Ensamble          ORBoost   
1004_synthetic_control_10_1.csv.gz  Ensamble          ORBoost   
1004_synthetic_control_10_2.csv.gz  Ensamble          ORBoost   
1004_synthetic_control_10_3.csv.gz  Ensamble          ORBoost   
1004_synthetic_control_10_4.csv.gz  Ensamble          ORBoost   
...                                      ...              ...   
997_balance-scale_5_5.csv.gz        Ensamble          ORBoost   
997_balance-scale_5_6.csv.gz        Ensamble          ORBoost   
997_balance-scale_5_7.csv.gz          Voting          ORBoost   
997_balance-scale_5_8.csv.gz        Ensamble          ORBoost   
997_balance-scale_5_9.csv.gz        Ensamble          ORBoost   

                                   BestDistanceAlgo BestVotingAlgo BestAenn  \
Dataset                                                                       
1004_synthetic_control_10_0.csv.gz             AENN        Dynamic   AENN11   
1004_synthetic_control_10_1.csv.gz             AENN        Dynamic   AENN11   
1004_synthetic_control_10_2.csv.gz             AENN        Dynamic   AENN11   
1004_synthetic_control_10_3.csv.gz             AENN        Dynamic   AENN11   
1004_synthetic_control_10_4.csv.gz             AENN        Dynamic   AENN11   
...                                             ...            ...      ...   
997_balance-scale_5_5.csv.gz                   AENN        Dynamic    AENN9   
997_balance-scale_5_6.csv.gz                   AENN        Dynamic   AENN11   
997_balance-scale_5_7.csv.gz                   AENN        Dynamic   AENN11   
997_balance-scale_5_8.csv.gz                   AENN        Dynamic    AENN9   
997_balance-scale_5_9.csv.gz                   AENN        Dynamic    AENN9   

                                   BestGE BestOR BestEdge BestHARF  
Dataset                                                             
1004_synthetic_control_10_0.csv.gz    GE9    OR3   Edge20   HARF70  
1004_synthetic_control_10_1.csv.gz    GE9    OR3   Edge20   HARF70  
1004_synthetic_control_10_2.csv.gz   GE11    OR7   Edge20   HARF70  
1004_synthetic_control_10_3.csv.gz    GE9    OR3   Edge20   HARF70  
1004_synthetic_control_10_4.csv.gz    GE9    OR7   Edge20   HARF70  
...                                   ...    ...      ...      ...  
997_balance-scale_5_5.csv.gz         GE11    OR3   Edge20   HARF70  
997_balance-scale_5_6.csv.gz          GE9    OR3   Edge20   HARF70  
997_balance-scale_5_7.csv.gz         GE11    OR3   Edge20   HARF70  
997_balance-scale_5_8.csv.gz         GE11   OR19   Edge20   HARF70  
997_balance-scale_5_9.csv.gz         GE11    OR3   Edge20   HARF70  

[10740 rows x 9 columns]

/tmp/ipykernel_1029168/1805131222.py:22: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rank = rank.append(meta_data.iloc[i].rank(method = 'dense', ascending = False))
/tmp/ipykernel_1029168/1805131222.py:22: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rank = rank.append(meta_data.iloc[i].rank(method = 'dense', ascending = False))
/tmp/ipykernel_1029168/1805131222.py:22: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rank = rank.append(meta_data.iloc[i].rank(method = 'dense', ascending = False))
/tmp/ipykernel_1029168/1805131222.py:22: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rank = rank.append(meta_data.iloc[i].rank(method = 'dens

SelectedAlgo       Best
1004_synthetic_control_10_0.csv.gz          OR3   [AENN11]
1004_synthetic_control_10_1.csv.gz          OR3  [Dynamic]
1004_synthetic_control_10_2.csv.gz          OR7  [Dynamic]
1004_synthetic_control_10_3.csv.gz          OR3   [Hybrid]
1004_synthetic_control_10_4.csv.gz          OR7     [OR11]
...                                         ...        ...
997_balance-scale_5_5.csv.gz                OR3    [AENN5]
997_balance-scale_5_6.csv.gz                OR3    [AENN3]
997_balance-scale_5_7.csv.gz            Dynamic    [AENN9]
997_balance-scale_5_8.csv.gz               OR19    [AENN9]
997_balance-scale_5_9.csv.gz                OR3    [AENN7]

[10740 rows x 2 columns]

Empty DataFrame
Columns: [SelectedAlgo, Best]
Index: []

In [56]:
df0 [df0['SelectedAlgo'].isin(df0['Best'])]
arr = []
for index, row in df0.iterrows():
    arr.append(row['SelectedAlgo'] in row['Best'])
sum(arr)

3433

In [51]:
meta_data = pd.read_csv(f'Metabases/Metabase_DT.csv.zip', index_col='Dataset').iloc[:,97:]
rank = pd.DataFrame()
meta_data.drop('test_f1_macro_mean_AENN',axis=1, inplace=True)
for i, a in enumerate(meta_data.index):
    rank = rank.append(meta_data.iloc[i].rank(method = 'dense', ascending = False))

rank.columns = ['Edge5','Edge20', 'HARF85','Hybrid', 'OR3','GE9', 'AENN7',
    'HARF75', 'OR19','AENN11', 'AENN9','OR11', 'PRISM','GE3', 'GE7',
    'OR15', 'Dynamic','Edge10', 'HARF80','AENN3', 'HARF90','OR7', 'HARF70',
    'GE5', 'AENN5','GE11']


/tmp/ipykernel_1029168/4058997559.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rank = rank.append(meta_data.iloc[i].rank(method = 'dense', ascending = False))
/tmp/ipykernel_1029168/4058997559.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rank = rank.append(meta_data.iloc[i].rank(method = 'dense', ascending = False))
/tmp/ipykernel_1029168/4058997559.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rank = rank.append(meta_data.iloc[i].rank(method = 'dense', ascending = False))
/tmp/ipykernel_1029168/4058997559.py:5: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  rank = rank.append(meta_data.iloc[i].rank(method = 'dense', 

In [98]:
# rank.value_counts()
import plotly.express as px
df0 [df0['SelectedAlgo'].isin(df0['Best'])]
arr = []
for index, row in df0.iterrows():
    arr.append(row['SelectedAlgo'] in row['Best'])

a = rank.apply(pd.value_counts)
a['MtL'] = sum(arr)
a['MtL-ranking'] = sum(arr2)
fig = px.bar(a.iloc[0].sort_values(ascending = False))
fig.show()
# rank.apply(pd.value_counts).iloc[0]

In [67]:
meta_data.columns = ['Edge5','Edge20', 'HARF85','Hybrid', 'OR3','GE9', 'AENN7',
    'HARF75', 'OR19','AENN11', 'AENN9','OR11', 'Prism','GE3', 'GE7',
    'OR15', 'Dynamic','Edge10', 'HARF80','AENN3', 'HARF90','OR7', 'HARF70',
    'GE5', 'AENN5','GE11']
meta_data

totalF1 = 0
for index, row in df0.iterrows():
    totalF1 +=meta_data[row['SelectedAlgo']].loc[index]
totalF1

8393.805876259137

In [89]:
RFPredictRank = pd.read_csv('RankingResults/results_RF_f1-score-DT.csv.zip', index_col='Dataset')
RFPredictRank.drop('test_f1_macro_mean_AENN', axis=1, inplace=True)
rank2 = pd.DataFrame()
for i, a in enumerate(RFPredictRank.index):
    rank2 = rank2.append(RFPredictRank.iloc[i].rank(method = 'dense', ascending = False))
rank2

/tmp/ipykernel_1029168/3051558711.py:5: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

/tmp/ipykernel_1029168/3051558711.py:5: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

/tmp/ipykernel_1029168/3051558711.py:5: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

/tmp/ipykernel_1029168/3051558711.py:5: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

/tmp/ipykernel_1029168/3051558711.py:5: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

/tmp/ipykernel_1029168/3051558711.py:5: FutureWarning:

The frame.append method is deprecated and will be removed from pandas

test_f1_macro_mean_edgeBoostFilter-5  \
1004_synthetic_control_10_0.csv.gz                                  26.0   
1004_synthetic_control_10_1.csv.gz                                  26.0   
1004_synthetic_control_10_2.csv.gz                                  26.0   
1004_synthetic_control_10_3.csv.gz                                  21.0   
1004_synthetic_control_10_4.csv.gz                                  26.0   
...                                                                  ...   
997_balance-scale_5_5.csv.gz                                        25.0   
997_balance-scale_5_6.csv.gz                                        25.0   
997_balance-scale_5_7.csv.gz                                        25.0   
997_balance-scale_5_8.csv.gz                                        25.0   
997_balance-scale_5_9.csv.gz                                        25.0   

                                    test_f1_macro_mean_edgeBoostFilter-20  \
1004_synthetic_control_10_0.csv.gz                                   18.0   
1004_synthetic_control_10_1.csv.gz                                   18.0   
1004_synthetic_control_10_2.csv.gz                                   17.0   
1004_synthetic_control_10_3.csv.gz                                   17.0   
1004_synthetic_control_10_4.csv.gz                                   22.0   
...                                                                   ...   
997_balance-scale_5_5.csv.gz                                         18.0   
997_balance-scale_5_6.csv.gz                                         19.0   
997_balance-scale_5_7.csv.gz                                         19.0   
997_balance-scale_5_8.csv.gz                                         18.0   
997_balance-scale_5_9.csv.gz                                         18.0   

                                    test_f1_macro_mean_HARF-85  \
1004_synthetic_control_10_0.csv.gz                        20.0   
1004_synthetic_control_10_1.csv.gz                        19.0   
1004_synthetic_control_10_2.csv.gz                        21.0   
1004_synthetic_control_10_3.csv.gz                        15.0   
1004_synthetic_control_10_4.csv.gz                        21.0   
...                                                        ...   
997_balance-scale_5_5.csv.gz                              21.0   
997_balance-scale_5_6.csv.gz                              21.0   
997_balance-scale_5_7.csv.gz                              21.0   
997_balance-scale_5_8.csv.gz                              21.0   
997_balance-scale_5_9.csv.gz                              21.0   

                                    test_f1_macro_mean_hybridRepairFilter  \
1004_synthetic_control_10_0.csv.gz                                    2.0   
1004_synthetic_control_10_1.csv.gz                                    2.0   
1004_synthetic_control_10_2.csv.gz                                    3.0   
1004_synthetic_control_10_3.csv.gz                                    2.0   
1004_synthetic_control_10_4.csv.gz                                    2.0   
...                                                                   ...   
997_balance-scale_5_5.csv.gz                                          5.0   
997_balance-scale_5_6.csv.gz                                          6.0   
997_balance-scale_5_7.csv.gz                                          6.0   
997_balance-scale_5_8.csv.gz                                          6.0   
997_balance-scale_5_9.csv.gz                                          6.0   

                                    test_f1_macro_mean_ORBoost-3  \
1004_synthetic_control_10_0.csv.gz                          21.0   
1004_synthetic_control_10_1.csv.gz                          22.0   
1004_synthetic_control_10_2.csv.gz                          22.0   
1004_synthetic_control_10_3.csv.gz                          22.0   
1004_synthetic_control_10_4.csv.gz                          16.0   
...                                                          ...   
997_

In [91]:
rank2.idxmin(axis =1)

1004_synthetic_control_10_0.csv.gz    Dynamic
1004_synthetic_control_10_1.csv.gz    Dynamic
1004_synthetic_control_10_2.csv.gz    Dynamic
1004_synthetic_control_10_3.csv.gz    Dynamic
1004_synthetic_control_10_4.csv.gz    Dynamic
                                       ...   
997_balance-scale_5_5.csv.gz          Dynamic
997_balance-scale_5_6.csv.gz          Dynamic
997_balance-scale_5_7.csv.gz          Dynamic
997_balance-scale_5_8.csv.gz          Dynamic
997_balance-scale_5_9.csv.gz          Dynamic
Length: 10740, dtype: object

In [97]:
total = 0
# rank2.columns = ['Edge5','Edge20', 'HARF85','Hybrid', 'OR3','GE9', 'AENN7',
#     'HARF75', 'OR19','AENN11', 'AENN9','OR11', 'Prism','GE3', 'GE7',
#     'OR15', 'Dynamic','Edge10', 'HARF80','AENN3', 'HARF90','OR7', 'HARF70',
#     'GE5', 'AENN5','GE11']
arr2 = []
# for index, row in df0.iterrows():
    
for index, value  in enumerate(rank2.idxmin(axis =1)):
    total += meta_data[value].iloc[index]
    arr2.append(value in df0['Best'].iloc[index])
    # print(row)
# arr2 =[]
# for index, row in rank2.iterrows():
#         arr2 = list(row[row == 1].index)
display(total)
sum(arr2)

9035.085753627005

3091

In [94]:
a = meta_data.sum()
a['MtL'] = totalF1
a['mtl-Ranking'] = total
fig = px.bar(a.sort_values(ascending=False))
fig.show()